In [1]:
from pathlib import Path
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import sklearn
import ydata_profiling
from skrub import TableReport
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.linear_model import Lasso
from sklearn.linear_model import ElasticNet
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer


In [2]:
data = pd.read_parquet(Path("data") / "train.parquet")
data.head()

counter_id              counter_name    site_id  \
48321  100007049-102007049  28 boulevard Diderot E-O  100007049   
48324  100007049-102007049  28 boulevard Diderot E-O  100007049   
48327  100007049-102007049  28 boulevard Diderot E-O  100007049   
48330  100007049-102007049  28 boulevard Diderot E-O  100007049   
48333  100007049-102007049  28 boulevard Diderot E-O  100007049   

                  site_name  bike_count                date  \
48321  28 boulevard Diderot         0.0 2020-09-01 02:00:00   
48324  28 boulevard Diderot         1.0 2020-09-01 03:00:00   
48327  28 boulevard Diderot         0.0 2020-09-01 04:00:00   
48330  28 boulevard Diderot         4.0 2020-09-01 15:00:00   
48333  28 boulevard Diderot         9.0 2020-09-01 18:00:00   

      counter_installation_date         coordinates counter_technical_id  \
48321                2013-01-18  48.846028,2.375429          Y2H15027244   
48324                2013-01-18  48.846028,2.375429          Y2H15027244   
48327                2013-01-18  48.846028,2.375429          Y2H15027244   
48330                2013-01-18  48.846028,2.375429          Y2H15027244   
48333                2013-01-18  48.846028,2.375429          Y2H15027244   

        latitude  longitude  log_bike_count  
48321  48.846028   2.375429        0.000000  
48324  48.846028   2.375429        0.693147  
48327  48.846028   2.375429        0.000000  
48330  48.846028   2.375429        1.609438  
48333  48.846028   2.375429        2.302585

In [3]:
external_conditions = pd.read_csv('data/external_data.csv')
external_conditions.head()

numer_sta                 date    pmer  tend  cod_tend   dd   ff       t  \
0       7149  2021-01-01 00:00:00  100810    80         1  270  1.8  272.75   
1       7149  2021-01-01 03:00:00  100920   110         3  300  1.7  271.25   
2       7149  2021-01-01 06:00:00  100950    30         3  290  2.6  271.95   
3       7149  2021-01-01 09:00:00  101100   150         2  280  1.7  272.45   
4       7149  2021-01-01 12:00:00  101110    30         0   50  1.0  276.95   

       td   u  ...  hnuage1  nnuage2  ctype2  hnuage2  nnuage3  ctype3  \
0  272.15  96  ...    600.0      NaN     NaN      NaN      NaN     NaN   
1  270.95  98  ...   1500.0      2.0     3.0   3000.0      NaN     NaN   
2  271.65  98  ...    480.0      4.0     6.0   2000.0      6.0     3.0   
3  272.05  97  ...   1740.0      3.0     3.0   2800.0      NaN     NaN   
4  274.15  82  ...    330.0      4.0     6.0    570.0      7.0     6.0   

   hnuage3  nnuage4  ctype4  hnuage4  
0      NaN      NaN     NaN      NaN  
1      NaN      NaN     NaN      NaN  
2   3000.0      NaN     NaN      NaN  
3      NaN      NaN     NaN      NaN  
4    810.0      NaN     NaN      NaN  

[5 rows x 59 columns]

In [4]:
# Dictionary mapping column names to their practical explanations
column_name_mapping = {
    'numer_sta': 'Station Number',
    'date': 'Date and Time',
    'pmer': 'Sea Level Pressure (hPa)',
    'tend': 'Pressure Tendency (hPa/3h)',
    'cod_tend': 'Pressure Tendency Code',
    'dd': 'Wind Direction (°)',
    'ff': 'Wind Speed (m/s)',
    't': 'Air Temperature (°C)',
    'td': 'Dew Point Temperature (°C)',
    'u': 'Relative Humidity (%)',
    'vv': 'Visibility (m)',
    'ww': 'Present Weather Code',
    'w1': 'Past Weather Code 1',
    'w2': 'Past Weather Code 2',
    'n': 'Total Cloud Cover (oktas)',
    'nbas': 'Cloud Base Height (m)',
    'hbas': 'Lowest Cloud Base Height (m)',
    'cl': 'Low Cloud Type',
    'cm': 'Medium Cloud Type',
    'ch': 'High Cloud Type',
    'pres': 'Station Level Pressure (hPa)',
    'niv_bar': 'Barometer Altitude (m)',
    'geop': 'Geopotential Height (m)',
    'tend24': '24h Pressure Tendency (hPa)',
    'tn12': '12h Minimum Temperature (°C)',
    'tn24': '24h Minimum Temperature (°C)',
    'tx12': '12h Maximum Temperature (°C)',
    'tx24': '24h Maximum Temperature (°C)',
    'tminsol': 'Minimum Soil Temperature (°C)',
    'sw': 'Sunshine Duration (hours)',
    'tw': 'Wet Bulb Temperature (°C)',
    'raf10': '10min Max Wind Gust (m/s)',
    'rafper': 'Max Wind Gust (m/s)',
    'per': 'Measurement Period Duration',
    'etat_sol': 'Ground State',
    'ht_neige': 'Snow Height (cm)',
    'ssfrai': 'New Snow Depth (cm)',
    'perssfrai': 'New Snowfall Duration (hours)',
    'rr1': 'Rainfall (1h, mm)',
    'rr3': 'Rainfall (3h, mm)',
    'rr6': 'Rainfall (6h, mm)',
    'rr12': 'Rainfall (12h, mm)',
    'rr24': 'Rainfall (24h, mm)',
    'phenspe1': 'Special Weather Phenomenon 1',
    'phenspe2': 'Special Weather Phenomenon 2',
    'phenspe3': 'Special Weather Phenomenon 3',
    'phenspe4': 'Special Weather Phenomenon 4',
    'nnuage1': 'Layer 1 Cloud Cover (oktas)',
    'ctype1': 'Layer 1 Cloud Type',
    'hnuage1': 'Layer 1 Cloud Base Height (m)',
    'nnuage2': 'Layer 2 Cloud Cover (oktas)',
    'ctype2': 'Layer 2 Cloud Type',
    'hnuage2': 'Layer 2 Cloud Base Height (m)',
    'nnuage3': 'Layer 3 Cloud Cover (oktas)',
    'ctype3': 'Layer 3 Cloud Type',
    'hnuage3': 'Layer 3 Cloud Base Height (m)',
    'nnuage4': 'Layer 4 Cloud Cover (oktas)',
    'ctype4': 'Layer 4 Cloud Type',
    'hnuage4': 'Layer 4 Cloud Base Height (m)',
}

# Rename columns in the DataFrame
external_conditions = external_conditions.rename(columns=column_name_mapping)


In [5]:
threshold = len(external_conditions) * 0.8
external_conditions = external_conditions.loc[:, external_conditions.isnull().sum() < threshold]
TableReport(external_conditions)

Processing column  42 / 42


<TableReport: use .open() to display>

In [6]:
# Convert 'Date and Time' column in external_conditions to datetime
external_conditions['Date and Time'] = pd.to_datetime(external_conditions['Date and Time'])

# Merge the dataframes
merged_data = pd.merge(data, external_conditions, left_on='date', right_on='Date and Time', how='inner')

# Display the merged dataframe
merged_data.head(15)

counter_id              counter_name    site_id  \
0   100007049-102007049  28 boulevard Diderot E-O  100007049   
1   100007049-102007049  28 boulevard Diderot E-O  100007049   
2   100007049-102007049  28 boulevard Diderot E-O  100007049   
3   100007049-102007049  28 boulevard Diderot E-O  100007049   
4   100007049-102007049  28 boulevard Diderot E-O  100007049   
5   100007049-102007049  28 boulevard Diderot E-O  100007049   
6   100007049-102007049  28 boulevard Diderot E-O  100007049   
7   100007049-102007049  28 boulevard Diderot E-O  100007049   
8   100007049-102007049  28 boulevard Diderot E-O  100007049   
9   100007049-102007049  28 boulevard Diderot E-O  100007049   
10  100007049-102007049  28 boulevard Diderot E-O  100007049   
11  100007049-102007049  28 boulevard Diderot E-O  100007049   
12  100007049-102007049  28 boulevard Diderot E-O  100007049   
13  100007049-102007049  28 boulevard Diderot E-O  100007049   
14  100007049-102007049  28 boulevard Diderot E-O  100007049   

               site_name  bike_count                date  \
0   28 boulevard Diderot         1.0 2020-09-01 03:00:00   
1   28 boulevard Diderot         4.0 2020-09-01 15:00:00   
2   28 boulevard Diderot         9.0 2020-09-01 18:00:00   
3   28 boulevard Diderot         7.0 2020-09-02 18:00:00   
4   28 boulevard Diderot        12.0 2020-09-03 15:00:00   
5   28 boulevard Diderot         0.0 2020-09-03 21:00:00   
6   28 boulevard Diderot         3.0 2020-09-04 09:00:00   
7   28 boulevard Diderot         5.0 2020-09-04 12:00:00   
8   28 boulevard Diderot         1.0 2020-09-04 18:00:00   
9   28 boulevard Diderot         1.0 2020-09-04 21:00:00   
10  28 boulevard Diderot         0.0 2020-09-05 00:00:00   
11  28 boulevard Diderot         0.0 2020-09-05 03:00:00   
12  28 boulevard Diderot         3.0 2020-09-05 06:00:00   
13  28 boulevard Diderot         3.0 2020-09-05 12:00:00   
14  28 boulevard Diderot         4.0 2020-09-01 09:00:00   

   counter_installation_date         coordinates counter_technical_id  \
0                 2013-01-18  48.846028,2.375429          Y2H15027244   
1                 2013-01-18  48.846028,2.375429          Y2H15027244   
2                 2013-01-18  48.846028,2.375429          Y2H15027244   
3                 2013-01-18  48.846028,2.375429          Y2H15027244   
4                 2013-01-18  48.846028,2.375429          Y2H15027244   
5                 2013-01-18  48.846028,2.375429          Y2H15027244   
6                 2013-01-18  48.846028,2.375429          Y2H15027244   
7                 2013-01-18  48.846028,2.375429          Y2H15027244   
8                 2013-01-18  48.846028,2.375429          Y2H15027244   
9                 2013-01-18  48.846028,2.375429          Y2H15027244   
10                2013-01-18  48.846028,2.375429          Y2H15027244   
11                2013-01-18  48.846028,2.375429          Y2H15027244   
12                2013-01-18  48.846028,2.375429          Y2H15027244   
13                2013-01-18  48.846028,2.375429          Y2H15027244   
14                2013-01-18  48.846028,2.375429          Y2H15027244   

     latitude  ...  Rainfall (3h, mm)  Rainfall (6h, mm)  Rainfall (12h, mm)  \
0   48.846028  ...                0.0                0.0                 0.0   
1   48.846028  ...                0.0                0.0                 0.0   
2   48.846028  ...                0.0                0.0                 0.0   
3   48.846028  ...                0.0                0.0                 0.0   
4   48.846028  ...                0.0                0.0                 0.0   
5   48.846028  ...                0.0                0.0                 0.0   
6   48.846028  ...                0.0                0.0                 0.0   
7   48.846028  ...                0.0                0.0                 0.0   
8   48.846028  ...                0.0                0.0                 0.0   
9   48.846028  ...                0.0                0.0  

In [7]:
# Extract date and time features
merged_data['measurement_year'] = merged_data['Date and Time'].dt.year
merged_data['measurement_month'] = merged_data['Date and Time'].dt.month
merged_data['measurement_day'] = merged_data['Date and Time'].dt.day
merged_data['measurement_hour'] = merged_data['Date and Time'].dt.hour

merged_data['counter_year'] = merged_data['Date and Time'].dt.year
merged_data['counter_month'] = merged_data['Date and Time'].dt.month
merged_data['counter_day'] = merged_data['Date and Time'].dt.day
merged_data['counter_hour'] = merged_data['Date and Time'].dt.hour

merged_data

counter_id                counter_name    site_id  \
0       100007049-102007049    28 boulevard Diderot E-O  100007049   
1       100007049-102007049    28 boulevard Diderot E-O  100007049   
2       100007049-102007049    28 boulevard Diderot E-O  100007049   
3       100007049-102007049    28 boulevard Diderot E-O  100007049   
4       100007049-102007049    28 boulevard Diderot E-O  100007049   
...                     ...                         ...        ...   
165363  300014702-353245971  254 rue de Vaugirard SO-NE  300014702   
165364  300014702-353245971  254 rue de Vaugirard SO-NE  300014702   
165365  300014702-353245971  254 rue de Vaugirard SO-NE  300014702   
165366  300014702-353245971  254 rue de Vaugirard SO-NE  300014702   
165367  300014702-353245971  254 rue de Vaugirard SO-NE  300014702   

                   site_name  bike_count                date  \
0       28 boulevard Diderot         1.0 2020-09-01 03:00:00   
1       28 boulevard Diderot         4.0 2020-09-01 15:00:00   
2       28 boulevard Diderot         9.0 2020-09-01 18:00:00   
3       28 boulevard Diderot         7.0 2020-09-02 18:00:00   
4       28 boulevard Diderot        12.0 2020-09-03 15:00:00   
...                      ...         ...                 ...   
165363  254 rue de Vaugirard       211.0 2021-09-07 15:00:00   
165364  254 rue de Vaugirard       156.0 2021-09-09 18:00:00   
165365  254 rue de Vaugirard       440.0 2021-09-08 06:00:00   
165366  254 rue de Vaugirard       445.0 2021-09-09 06:00:00   
165367  254 rue de Vaugirard       218.0 2021-09-09 15:00:00   

       counter_installation_date         coordinates counter_technical_id  \
0                     2013-01-18  48.846028,2.375429          Y2H15027244   
1                     2013-01-18  48.846028,2.375429          Y2H15027244   
2                     2013-01-18  48.846028,2.375429          Y2H15027244   
3                     2013-01-18  48.846028,2.375429          Y2H15027244   
4                     2013-01-18  48.846028,2.375429          Y2H15027244   
...                          ...                 ...                  ...   
165363                2020-11-29    48.83977,2.30198          Y2H20114504   
165364                2020-11-29    48.83977,2.30198          Y2H20114504   
165365                2020-11-29    48.83977,2.30198          Y2H20114504   
165366                2020-11-29    48.83977,2.30198          Y2H20114504   
165367                2020-11-29    48.83977,2.30198          Y2H20114504   

         latitude  ...  Layer 2 Cloud Type  Layer 2 Cloud Base Height (m)  \
0       48.846028  ...                 NaN                            NaN   
1       48.846028  ...                 6.0                         2300.0   
2       48.846028  ...                 6.0                         2400.0   
3       48.846028  ...                 NaN                            NaN   
4       48.846028  ...                 0.0                         8000.0   
...           ...  ...                 ...                            ...   
165363  48.839770  ...                 NaN                            NaN   
165364  48.839770  ...                 3.0                         2800.0   
165365  48.839770  ...                 NaN                            NaN   
165366  48.839770  ...                 NaN                            NaN   
165367  48.839770  ...                 6.0                         1560.0   

        measurement_year measurement_month  measurement_day  measurement_hour  \
0                   2020                 9                1                 3   
1                   2020                 9                1                15   
2                   2020                 9                1                18   
3                   2020                 9                2                18   
4                   2020                 9                3                15   
...                  ...               ...              ...            

In [8]:
TableReport(merged_data)

Processing column  62 / 62


<TableReport: use .open() to display>

Decide to remove site id, site name and counter id to just keep counter name to reduce complexity and the data as they all provide more or less the same information. Counter is more precise as we will be able to calculate the number of times a counter is used in a given site.

## Model training with Elastic Net (To find the best features)

Elastic net can handle multicolinearity and shrinks the less important features to zero. It is a combination of L1 and L2 regularization. It is a linear regression model trained with L1 and L2 prior as regularizer. This combination allows for learning a sparse model where few of the weights are non-zero like Lasso, while still maintaining the regularization properties of Ridge.

In [ ]:
# Define the features and target variable
X = merged_data.drop(columns=[
                            'bike_count', 'log_bike_count',
                            'counter_id', 'site_id', 'site_name', 'counter_technical_id',
                            'coordinates',
                            'Station Number', 'Measurement Period Duration',
                            'date', 'Date and Time', 'counter_installation_date',
                    ])

y = merged_data['log_bike_count']

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Define the column transformer with OneHotEncoder for 'counter_name' and SimpleImputer for numerical columns
preprocessor = ColumnTransformer(
    transformers=[
        ('num', SimpleImputer(strategy='mean'), X.select_dtypes(include=['float64', 'int64']).columns),
        ('cat', OneHotEncoder(handle_unknown='ignore'), ['counter_name'])
    ])

# Create a pipeline with the preprocessor, standard scaler, and ElasticNet regression
elasticnet_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('scaler', StandardScaler()),
    ('regressor', ElasticNet(alpha=0.1, l1_ratio=0.5))
])

# Fit the ElasticNet pipeline on the training data
elasticnet_pipeline.fit(X_train, y_train)

# Print the score of the ElasticNet model on the test data
print(f"ElasticNet model score: {elasticnet_pipeline.score(X_test, y_test)}")

# Output information about the ElasticNet model
elasticnet_coefficients = elasticnet_pipeline.named_steps['regressor'].coef_

# Get feature names after preprocessing
feature_names = (elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[0][2].tolist() +  # numerical features
                 elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[1][1].get_feature_names_out(['counter_name']).tolist())  # one-hot encoded features
elasticnet_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('scaler', StandardScaler()),
    ('regressor', ElasticNet(alpha=0.1, l1_ratio=0.5))
])

# Fit the ElasticNet pipeline on the training data
elasticnet_pipeline.fit(X_train, y_train)

# Print the score of the ElasticNet model on the test data
print(f"ElasticNet model score: {elasticnet_pipeline.score(X_test, y_test)}")

# Output information about the ElasticNet model
elasticnet_coefficients = elasticnet_pipeline.named_steps['regressor'].coef_

# Get feature names after preprocessing
feature_names = (elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[0][2].tolist() +  # numerical features
                 elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[1][1].get_feature_names_out(['counter_name']).tolist())  # one-hot encoded features
elasticnet_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('scaler', StandardScaler()),
    ('regressor', ElasticNet(alpha=0.1, l1_ratio=0.5))
])

# Fit the ElasticNet pipeline on the training data
elasticnet_pipeline.fit(X_train, y_train)

# Print the score of the ElasticNet model on the test data
print(f"ElasticNet model score: {elasticnet_pipeline.score(X_test, y_test)}")

# Output information about the ElasticNet model
elasticnet_coefficients = elasticnet_pipeline.named_steps['regressor'].coef_

# Get feature names after preprocessing
feature_names = (elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[0][2].tolist() +  # numerical features
                 elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[1][1].get_feature_names_out(['counter_name']).tolist())  # one-hot encoded features
elasticnet_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('scaler', StandardScaler()),
    ('regressor', ElasticNet(alpha=0.1, l1_ratio=0.5))
])

# Fit the ElasticNet pipeline on the training data
elasticnet_pipeline.fit(X_train, y_train)

# Print the score of the ElasticNet model on the test data
print(f"ElasticNet model score: {elasticnet_pipeline.score(X_test, y_test)}")

# Output information about the ElasticNet model
elasticnet_coefficients = elasticnet_pipeline.named_steps['regressor'].coef_

# Get feature names after preprocessing
feature_names = (elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[0][2].tolist() +  # numerical features
                 elasticnet_pipeline.named_steps['preprocessor']
                 .transformers_[1][1].get_feature_names_out(['counter_name']).tolist())  # one-hot encoded features

elasticnet_feature_importance = pd.Series(elasticnet_coefficients, index=feature_names).sort_values(ascending=False)

ElasticNet model score: 0.31554749950859085


In [10]:
# Print the feature importances
print(elasticnet_feature_importance)

Air Temperature (°C)                                 0.299430
counter_name_Totem 73 boulevard de Sébastopol S-N    0.146886
counter_name_Totem 73 boulevard de Sébastopol N-S    0.121193
counter_name_Totem 64 Rue de Rivoli O-E              0.101785
Total Cloud Cover (oktas)                            0.080736
                                                       ...   
New Snowfall Duration (hours)                       -0.087010
counter_name_Face au 40 quai D'Issy NE-SO           -0.139527
counter_name_Face au 40 quai D'Issy SO-NE           -0.166229
counter_name_28 boulevard Diderot E-O               -0.227576
Relative Humidity (%)                               -0.384501
Length: 97, dtype: float64


In [14]:
# Filter features with non-zero importance
non_zero_features = elasticnet_feature_importance[elasticnet_feature_importance != 0].index.tolist()
# Keep only the non-zero features in the merged dataset
# Keep all the variables apart from the columns which are derived from a one hot encoder
non_zero_features = [feature for feature in non_zero_features if not feature.startswith('counter_name_')]
merged_data_filtered = merged_data[['counter_name', 'bike_count', 'log_bike_count'] + non_zero_features]

# Display the new dataframe
merged_data_filtered

counter_name  bike_count  log_bike_count  \
0         28 boulevard Diderot E-O         1.0        0.693147   
1         28 boulevard Diderot E-O         4.0        1.609438   
2         28 boulevard Diderot E-O         9.0        2.302585   
3         28 boulevard Diderot E-O         7.0        2.079442   
4         28 boulevard Diderot E-O        12.0        2.564949   
...                            ...         ...             ...   
165363  254 rue de Vaugirard SO-NE       211.0        5.356586   
165364  254 rue de Vaugirard SO-NE       156.0        5.056246   
165365  254 rue de Vaugirard SO-NE       440.0        6.089045   
165366  254 rue de Vaugirard SO-NE       445.0        6.100319   
165367  254 rue de Vaugirard SO-NE       218.0        5.389072   

        Air Temperature (°C)  Total Cloud Cover (oktas)  Low Cloud Type  \
0                     283.95                        0.0            30.0   
1                     293.65                       60.0            38.0   
2                     292.15                       90.0            38.0   
3                     292.75                        NaN             NaN   
4                     300.35                       75.0            35.0   
...                      ...                        ...             ...   
165363                302.95                       40.0            30.0   
165364                293.55                       90.0            39.0   
165365                290.45                       40.0            30.0   
165366                292.85                      100.0            32.0   
165367                299.35                       75.0            38.0   

        10min Max Wind Gust (m/s)  Max Wind Gust (m/s)   latitude  \
0                             1.5                  1.5  48.846028   
1                             7.5                  7.5  48.846028   
2                             6.5                  6.5  48.846028   
3                             3.7                  5.1  48.846028   
4                             7.7                  7.9  48.846028   
...                           ...                  ...        ...   
165363                       11.4                 12.5  48.839770   
165364                        4.9                 12.1  48.839770   
165365                        3.7                  3.7  48.839770   
165366                        4.3                  5.4  48.839770   
165367                        8.5                  9.7  48.839770   

        Pressure Tendency (hPa/3h)  24h Pressure Tendency (hPa)  \
0                              -60                          0.0   
1                             -110                       -260.0   
2                               10                       -210.0   
3                               60                        220.0   
4                              -50                        140.0   
...                            ...                          ...   
165363                        -220                       -400.0   
165364                          60                        150.0   
165365                         -90                       -800.0   
165366                         -10                       -230.0   
165367                         -70                         80.0   

        Cloud Base Height (m)  Present Weather Code  \
0                         0.0                     2   
1                         5.0                     3   
2                         7.0                     2   
3                         0.0                     0   
4                         3.0                     3   
...                       ...                   ...   
165363                    0.0                     3   
165364                    6.0                    25   
165365                    0.0                     3   
165366                    8.0                    10   
165367                    5.0                     2   

        Layer 2 Cloud Cover (okta

In [15]:
# Subtract 273 from all values in the "Air Temperature (°C)" column
# merged_data_filtered.loc[:,'Air Temperature (°C)'] -= 273
merged_data_filtered

counter_name  bike_count  log_bike_count  \
0         28 boulevard Diderot E-O         1.0        0.693147   
1         28 boulevard Diderot E-O         4.0        1.609438   
2         28 boulevard Diderot E-O         9.0        2.302585   
3         28 boulevard Diderot E-O         7.0        2.079442   
4         28 boulevard Diderot E-O        12.0        2.564949   
...                            ...         ...             ...   
165363  254 rue de Vaugirard SO-NE       211.0        5.356586   
165364  254 rue de Vaugirard SO-NE       156.0        5.056246   
165365  254 rue de Vaugirard SO-NE       440.0        6.089045   
165366  254 rue de Vaugirard SO-NE       445.0        6.100319   
165367  254 rue de Vaugirard SO-NE       218.0        5.389072   

        Air Temperature (°C)  Total Cloud Cover (oktas)  Low Cloud Type  \
0                     283.95                        0.0            30.0   
1                     293.65                       60.0            38.0   
2                     292.15                       90.0            38.0   
3                     292.75                        NaN             NaN   
4                     300.35                       75.0            35.0   
...                      ...                        ...             ...   
165363                302.95                       40.0            30.0   
165364                293.55                       90.0            39.0   
165365                290.45                       40.0            30.0   
165366                292.85                      100.0            32.0   
165367                299.35                       75.0            38.0   

        10min Max Wind Gust (m/s)  Max Wind Gust (m/s)   latitude  \
0                             1.5                  1.5  48.846028   
1                             7.5                  7.5  48.846028   
2                             6.5                  6.5  48.846028   
3                             3.7                  5.1  48.846028   
4                             7.7                  7.9  48.846028   
...                           ...                  ...        ...   
165363                       11.4                 12.5  48.839770   
165364                        4.9                 12.1  48.839770   
165365                        3.7                  3.7  48.839770   
165366                        4.3                  5.4  48.839770   
165367                        8.5                  9.7  48.839770   

        Pressure Tendency (hPa/3h)  24h Pressure Tendency (hPa)  \
0                              -60                          0.0   
1                             -110                       -260.0   
2                               10                       -210.0   
3                               60                        220.0   
4                              -50                        140.0   
...                            ...                          ...   
165363                        -220                       -400.0   
165364                          60                        150.0   
165365                         -90                       -800.0   
165366                         -10                       -230.0   
165367                         -70                         80.0   

        Cloud Base Height (m)  Present Weather Code  \
0                         0.0                     2   
1                         5.0                     3   
2                         7.0                     2   
3                         0.0                     0   
4                         3.0                     3   
...                       ...                   ...   
165363                    0.0                     3   
165364                    6.0                    25   
165365                    0.0                     3   
165366                    8.0                    10   
165367                    5.0                     2   

        Layer 2 Cloud Cover (okta

In [ ]:
from xgboost import XGBRegressor

# Define the features and target variable
X = merged_data.drop(columns=[
                            'bike_count', 'log_bike_count',
                    ])

y = merged_data['log_bike_count']

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Define the column transformer with OneHotEncoder for 'counter_name' and SimpleImputer for numerical columns
preprocessor = ColumnTransformer(
    transformers=[
        ('num', SimpleImputer(strategy='mean'), X.select_dtypes(include=['float64', 'int64']).columns),
        ('cat', OneHotEncoder(handle_unknown='ignore'), ['counter_name'])
    ])

# Create a pipeline with the preprocessor, standard scaler, and XGBRegressor
xgboostpipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('scaler', StandardScaler()),
    ('regressor', XGBRegressor())
])

# Fit the XGBRegressor pipeline on the training data
xgboostpipeline.fit(X_train, y_train)

# Print the score of the XGBRegressor model on the test data
print(f"XGBRegressor model score: {xgboostpipeline.score(X_test, y_test)}")

# Output information about the XGBRegressor model
xgboost_feature_importances = xgboostpipeline.named_steps['regressor'].feature_importances_

# Get feature names after preprocessing
feature_names = (xgboostpipeline.named_steps['preprocessor']
                 .transformers_[0][2].tolist() +  # numerical features
                 xgboostpipeline.named_steps['preprocessor']
                 .transformers_[1][1].get_feature_names_out(['counter_name']).tolist())  # one-hot encoded features


Note: you may need to restart the kernel to use updated packages.
XGBRegressor model score: 0.8431510119992153
